In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx
import seaborn as sns
import sys
import nolds as ns
import numba
import datetime
from numba import njit
from numba.typed import List
from sklearn.feature_selection import mutual_info_classif, mutual_info_regression
sys.path.insert(0, "D:/GIUSEPPE/Universita/TesiMagistrale/Kuramoto/Codice/modified")
%load_ext autoreload
%autoreload 2
from kuramoto.kuramoto import *
from kuramoto.plotting import *
# the above two lines are needed in order to see the modifications in python files without restarting vscode, 2 means that all modules will be reimported
sns.set_style("whitegrid")
sns.set_context("notebook", font_scale=1.6)

In [ ]:
def m_inf(f, delay):
    mi = np.empty(len(delay))
    for i in range(len(delay)):
        x = f[: len(f) - delay[i]]
        #x = x.reshape(-1,1)
        y = f[delay[i]: len(f)]
        y = y.reshape(-1,1)
        mi[i] = mutual_info_regression(y, x, n_neighbors=100)
    return mi


Varying only the coupling

In [ ]:
# Parameters
dt = 0.01 # time step
t_max = 100 # max time of the simulation
n_steps = int(t_max/dt)
A = 1
B = 8 # when the internal coupling is 0 there is chaotic behavior for B=5, periodic for lower values, such as B=2.5
# First network
N1 = 1000 # number of nodes
coupling1 = 0.0 # coupling between oscillators (will be normalized by the number of interactions)
omega_f1 = 1.0 # frequence of the external field

# Second network
N2 = 1000
coupling2 = 0.0
omega_f2 = omega_f1

# Varying  only the coupling between oscillators
# Parameters
c_max = 0.0 # maximum value of the coupling
c_points = 1 # number of coupling points


In [ ]:
# Vary only the coupling between the oscillators
print(f'Initial parameters')
print(f'number of nodes: N1 = {N1}, N2 = {N2}')
print(f'B = {B}')
print(f'external frequency = {omega_f1}')
print(f'time step dt = {dt}')
print(f'number of temporal steps {n_steps}')
lyap = []
now_0 = datetime.now()
print('Beginning of the simulation:', now_0, '\n')
for c in np.linspace(0, c_max, c_points):
    print('##############')
    print('##############')
    print('Coupling:', c)
    print('##############')
    print('##############')

    now1 = datetime.now()
    print('Current time:', now1)
    print('Elapsed time since the beginning:', now1 - now_0, '\n')
    
    model = Kuramoto_com(coupling1=c, coupling2 = c, dt=dt, t_max=t_max, n_nodes1=N1,
                            n_nodes2=N2,omega_f1 = omega_f1, omega_f2 = omega_f2, A = A, B = B)

    graph_nx1 = nx.erdos_renyi_graph(n = N1, p = 6/(N1-1), directed = False); title1 = 'Erdos-Renyi' # in order to get average degree 6
    graph_nx2 = nx.barabasi_albert_graph(N1, m = 3); title2 = 'Barabasi-Albert'
    graph1 = nx.to_numpy_array(graph_nx1)
    graph2 = nx.to_numpy_array(graph_nx2)
    act_mat = model.run(adj_mat1 = graph1, adj_mat2 = graph2)
    print(f'Calculated the time series \n')
    ord1 = [Kuramoto.phase_coherence(vec) for vec in act_mat[:N1].T]
    ord2 = [Kuramoto.phase_coherence(vec) for vec in act_mat[N1:N1+N2].T]
    print(f'Calculated the order parameters')

    # Calculation of the mutual information in order to get the proper delay 
    max_d = 1000
    delay = np.arange(max_d)
    mi = m_inf(np.array(ord1[300:]), delay)

    for i in range(1, max_d - 1):
        if mi[i]<mi[i-1] and mi[i]<mi[i+1]:
            lag = i
            break
    lyap_h =ns.lyap_r(ord1[2000:], emb_dim = 4, lag=lag, debug_plot=False, tau = 0.01, trajectory_len = 55, fit_offset = 15)
    print(f'Lyapunov exponent {lyap_h}')
    string = [f'c1 = c2 = {c}, le = {lyap_h}']
    lyap.append(string)
    print('\n')
    
    
now_f = datetime.now()
print('End of the simulation', now_f)
print('Total time of the simulation', now_f - now_0)

print(lyap)

Varying only B

In [21]:
# Parameters
dt = 0.01 # time step
t_max = 100 # max time of the simulation
n_steps = int(t_max/dt)
A = 1

# First network
N1 = 1000 # number of nodes
omega_f1 = 1.0 # frequence of the external field

# Second network
N2 = 1000
omega_f2 = omega_f1

# Varying  only the coupling between oscillators
# Parameters
c = 0.0

B_max = 11.5
B_points = 20

In [22]:
# Vary only the coupling between the oscillators
print(f'Initial parameters \n')
print(f'number of nodes: N1 = {N1}, N2 = {N2}')
print(f'coupling c = {c}')
print(f'external frequency = {omega_f1}')
print(f'time step dt = {dt}')
print(f'number of temporal steps {n_steps}')
lyap = []
now_0 = datetime.now()
print('Beginning of the simulation:', now_0, '\n')
for B in np.linspace(2.5, B_max, B_points):
    print('##############')
    print('##############')
    print('B:', B)
    print('##############')
    print('##############')

    now1 = datetime.now()
    print('Current time:', now1)
    print('Elapsed time since the beginning:', now1 - now_0, '\n')
    
    model = Kuramoto_com(coupling1=c, coupling2 = c, dt=dt, t_max=t_max, n_nodes1=N1,
                            n_nodes2=N2,omega_f1 = omega_f1, omega_f2 = omega_f2, A = A, B = B)

    graph_nx1 = nx.erdos_renyi_graph(n = N1, p = 6/(N1-1), directed = False); title1 = 'Erdos-Renyi' # in order to get average degree 6
    graph_nx2 = nx.barabasi_albert_graph(N1, m = 3); title2 = 'Barabasi-Albert'
    graph1 = nx.to_numpy_array(graph_nx1)
    graph2 = nx.to_numpy_array(graph_nx2)
    act_mat = model.run(adj_mat1 = graph1, adj_mat2 = graph2)
    print(f'Calculated the time series')
    ord1 = [Kuramoto.phase_coherence(vec) for vec in act_mat[:N1].T]
    ord2 = [Kuramoto.phase_coherence(vec) for vec in act_mat[N1:N1+N2].T]
    print(f'Calculated the order parameters')
    # Calculation of the mutual information in order to get the proper delay 
    max_d = 1000
    delay = np.arange(max_d)
    mi = m_inf(np.array(ord1[300:]), delay)

    for i in range(1, max_d - 1):
        if mi[i]<mi[i-1] and mi[i]<mi[i+1]:
            lag = i
            break
    lyap_h =ns.lyap_r(ord1[2000:], emb_dim = 4, lag=lag, debug_plot=False, tau = 0.01, trajectory_len = 55, fit_offset = 15)
    print(f'Lyapunov exponent {lyap_h}')
    string = [f'B = {B}, le = {lyap_h}']
    lyap.append(string)
    print('\n')
    
    
now_f = datetime.now()
print('End of the simulation', now_f)
print('Total time of the simulation', now_f - now_0)

print(lyap)

Initial parameters 

number of nodes: N1 = 1000, N2 = 1000
coupling c = 0.0
external frequency = 1.0
time step dt = 0.01
number of temporal steps 10000
Beginning of the simulation: 2025-03-11 14:59:32.851963 

##############
##############
B: 2.3
##############
##############
Current time: 2025-03-11 14:59:32.852783
Elapsed time since the beginning: 0:00:00.000820 

Calculated the time series
Calculated the order parameters


C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regressi

Lyapunov exponent 1.1766746730236264


##############
##############
B: 2.784210526315789
##############
##############
Current time: 2025-03-11 15:06:12.230505
Elapsed time since the beginning: 0:06:39.378542 

Calculated the time series
Calculated the order parameters


C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regressi

Lyapunov exponent 1.1259218671352762


##############
##############
B: 3.2684210526315787
##############
##############
Current time: 2025-03-11 15:13:03.288199
Elapsed time since the beginning: 0:13:30.436236 

Calculated the time series
Calculated the order parameters


...

Lyapunov exponent -0.23205268571347887


##############
##############
B: 11.015789473684208
##############
##############
Current time: 2025-03-11 17:22:20.771531
Elapsed time since the beginning: 2:22:47.919568 

Calculated the time series
Calculated the order parameters


C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regressi

Lyapunov exponent 0.6176642902163386


##############
##############
B: 11.5
##############
##############
Current time: 2025-03-11 17:27:48.414036
Elapsed time since the beginning: 2:28:15.562073 

Calculated the time series
Calculated the order parameters


C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regression(y, x, n_neighbors=100)
C:\Users\gacqu\AppData\Local\Temp\ipykernel_2136\745332658.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  mi[i] = mutual_info_regressi

Lyapunov exponent -0.15035216947298732


End of the simulation 2025-03-11 17:54:20.616991
Total time of the simulation 2:54:47.765028
[['B = 2.3, le = 1.1766746730236264'], ['B = 2.784210526315789, le = 1.1259218671352762'], ['B = 3.2684210526315787, le = 0.4863313034973826'], ['B = 3.7526315789473683, le = 0.4650737518322249'], ['B = 4.2368421052631575, le = 0.5810360998794951'], ['B = 4.721052631578947, le = 0.6648921168426536'], ['B = 5.205263157894736, le = 0.4885077140504045'], ['B = 5.689473684210526, le = 0.5111038704562029'], ['B = 6.173684210526315, le = 0.7172858186814824'], ['B = 6.657894736842104, le = 0.5207509924302467'], ['B = 7.142105263157894, le = 0.6574195406053468'], ['B = 7.626315789473684, le = 0.6618104688136416'], ['B = 8.110526315789473, le = 0.399650458383527'], ['B = 8.594736842105263, le = 0.5790777333584708'], ['B = 9.078947368421051, le = 0.7510015185558915'], ['B = 9.563157894736841, le = 0.547447167382152'], ['B = 10.047368421052632, le = 0.5805113074158

Varying both B and coupling

In [ ]:
# Parameters
dt = 0.01 # time step
t_max = 100 # max time of the simulation
n_steps = int(t_max/dt)
A = 1

# First network
N1 = 1000 # number of nodes
coupling1 = 0.0 # coupling between oscillators (will be normalized by the number of interactions)
omega_f1 = 1.0 # frequence of the external field

# Second network
N2 = 1000
coupling2 = 0.0
omega_f2 = omega_f1

# Varying  only the coupling between oscillators
# Parameters
c_max = 0.0 # maximum value of the coupling
c_points = 1 # number of coupling points

B_max = 10
B_points = 1

In [ ]:
# Vary B and the coupling between the oscillators

lyap = []
now_0 = datetime.now()
print('Beginning of the simulation:', now_0, '\n')
for c in np.linspace(0, c_max, c_points):
    l = []
    print('##############')
    print('##############')
    print('Coupling:', c)
    print('##############')
    print('##############')

    now1 = datetime.now()
    print('Current time:', now1)
    print('Elapsed time since the beginning:', now1 - now_0, '\n')
    for B in np.linspace(2.5, B_max, B_points):
        now1 = datetime.now()
        print('##############')
        print('B:', B)
        print('##############')
        print('Current time:', now1)
        print('Elapsed time since the beginning:', now1 - now_0, '\n')
        
        model = Kuramoto_com(coupling1=c, coupling2 = c, dt=dt, t_max=t_max, n_nodes1=N1,
                                n_nodes2=N2,omega_f1 = omega_f1, omega_f2 = omega_f2, A = A, B = B)

        graph_nx1 = nx.erdos_renyi_graph(n = N1, p = 6/(N1-1), directed = False); title1 = 'Erdos-Renyi' # in order to get average degree 6
        graph_nx2 = nx.barabasi_albert_graph(N1, m = 3); title2 = 'Barabasi-Albert'
        graph1 = nx.to_numpy_array(graph_nx1)
        graph2 = nx.to_numpy_array(graph_nx2)
        act_mat = model.run(adj_mat1 = graph1, adj_mat2 = graph2)
        ord1 = [Kuramoto.phase_coherence(vec) for vec in act_mat[:N1].T]
        ord2 = [Kuramoto.phase_coherence(vec) for vec in act_mat[N1:N1+N2].T]
        
        # Calculation of the mutual information in order to get the proper delay 
        max_d = 1000
        delay = np.arange(max_d)
        mi = m_inf(np.array(ord1[300:]), delay)

        for i in range(1, max_d - 1):
            if mi[i]<mi[i-1] and mi[i]<mi[i+1]:
                lag = i
                break
        lyap_h =ns.lyap_r(ord1[2000:], emb_dim = 4, lag=lag, debug_plot=False, tau = 0.01, trajectory_len = 55, fit_offset = 15)
        string = [f'c1 = c2 = {c}, B = {B}, le = {lyap_h}']
        l.append(string)
    lyap.append(l)
    print('\n')
    
    
now_f = datetime.now()
print('End of the simulation', now_f)
print('Total time of the simulation', now_f - now_0)

print(lyap)